<a href="https://colab.research.google.com/github/ZhuangweiKang/VU-AD/blob/master/knn.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [111]:
import pandas as pd
sys.path.insert(0,'../') 
import plotter as pltr
import numpy as np
from dim_reduce import *

# from google.colab import drive
# drive.mount('/content/drive/Cisco/')

## SMD Dataset

In [112]:
GROUP = 1
ENTITY = 3
SMD_BASE_PATH = '../Dataset/SMD/processed'

X_train = pd.read_csv('%s/train/machine-%d-%d.txt' % (SMD_BASE_PATH, GROUP, ENTITY), index_col=0)
X_test = pd.read_csv('%s/test/machine-%d-%d.txt' % (SMD_BASE_PATH, GROUP, ENTITY), index_col=0)

y_test = pd.read_csv('../Dataset/SMD/test_label/machine-%d-%d.txt' % (GROUP, ENTITY), header=None)
y_test.columns = ['label']
y_test.index = X_test.index

# remove all-zero columns that are in training or testing set
train_nonzero_cols = X_train.columns[(X_train != 0).any()]
test_nonzero_cols = X_test.columns[(X_test != 0).any()]
cols = set(train_nonzero_cols) & set(test_nonzero_cols)

X_train = X_train[cols]
X_test = X_test[cols]

train_index = X_train.index
train_lines = X_train.shape[0]
test_index = X_test.index
test_lines = X_test.shape[0]

X = pd.concat([X_train, X_test], axis=0)

In [113]:
col = 'm0'
pltr.plot_data(X, col)

In [114]:
# Use PCA to create latent factor space
X = pca_dr(X, 0.90, transform=True)
X = pd.DataFrame(X, columns=['lm%d' % i for i in range(X.shape[1])], index=list(X_train.index)+list(X_test.index))

X_train = X.iloc[:train_lines]
X_test = X.iloc[train_lines:]

Number of factors: 2
Explained variance ratio of each factor: [0.86342466 0.09016277]
Explained variance of each factor:: [0.47625191 0.04973241]
Total explained variance ratio: 0.9535874279397383


In [115]:
from sklearn.preprocessing import MinMaxScaler

X_train = MinMaxScaler().fit_transform(X_train)
X_test = MinMaxScaler().fit_transform(X_test)

X_train = pd.DataFrame(X_train, columns=['lm%d' % i for i in range(X_train.shape[1])], index=train_index)
X_test = pd.DataFrame(X_test, columns=['lm%d' % i for i in range(X_test.shape[1])], index=test_index)

In [116]:
lcol = 'lm0'
pltr.plot_anomaly(X_test, y_test, lcol)

In [120]:
from pyod.models.knn import KNN

# outlier portion in testing set
anomaly_por = y_test[y_test['label'] == 1].shape[0] / y_test.shape[0]

# train kNN detector
clf_name = 'KNN'
clf = KNN(contamination=anomaly_por, n_neighbors=20)
clf.fit(X_train)

# get the prediction labels and outlier scores of the training data
y_train_pred = clf.labels_  # binary labels (0: inliers, 1: outliers)
y_train_scores = clf.decision_scores_  # raw outlier scores

# get the prediction on the test data
y_test_pred = clf.predict(X_test)  # outlier labels (0 or 1)
y_test_scores = clf.decision_function(X_test)  # outlier scores


In [121]:
from pyod.utils.data import evaluate_print

# evaluate and print the results
print("\nOn Test Data:")
evaluate_print(clf_name, y_test, y_test_scores)


On Test Data:
KNN ROC:0.3821, precision @ rank n:0.0012


In [122]:
threshold = 0.15

y_test_pred_label = pd.DataFrame(y_test_scores, columns=['label'], index=X_test.index)
y_test_pred_label['label'] = y_test_pred_label['label'] > threshold
pltr.plot_anomaly(X_test, y_test_pred_label, lcol)